In [74]:
import csv
import organize_functions
from os import listdir
import numpy as np
import re
import pandas as pd
import pprint
import sort_bus_by_date
from IPython.display import HTML  # For pretty printing!

In [2]:
directory = organize_functions.find_directory()

In [3]:
directory

'/mnt/d/Documents/Capstone/KCM-Data/Organization/Raw data/False_files_2/'

# Module for finding modules that are replaced.

In [104]:
def find_replaced_modules(directory):
    serial_index = 17
    bus_swapped_mods = {}  # Storing modules that have been swapped with each bus number
    for folder in listdir(directory):
        if folder.startswith('bus'):
            bus = folder
            bus_slash = folder + '/'
            replaced_mods = set()  # For storing modules that are confirmed swapped in and out
            modules_by_date = {}  # Storing every module per date
            serial_start_end = {}  # Storing each unique module (from set) and their starting and end times
            mod_set = set()  # A set (unordered, no repeats) of all module numbers in the bus folder
#             case of letter (i.e. to avoid A1 != a1)
            for file in listdir(directory + bus_slash):  # For each bus folder
                df = sort_bus_by_date.sort_bus_by_date(directory, bus_slash)  # Sarah's dataframe for organized files
                ordered_dates = []  # List of ordered dates per bus folder
                ordered_csv = df['Filename'].tolist()  # List of sorted CSV's by date
                ordered_unclean_dates = df['DateRetrieved'].tolist()  # List of sorted dates corresponding to CSVs
                for unclean_date in ordered_unclean_dates:
                    split_results = unclean_date.strftime('%m/%d/%Y, %H:%M:%S')
                    ordered_dates.append(split_results)  # Organized dates as strings
#                 print(ordered_dates)

                for i in range(len(ordered_csv)):
                    serials_in_csv = []
                    file_path = directory + bus_slash + ordered_csv[i]
                    with open(file_path) as file:
                        reader = csv.reader(file)
                        for row in reader:
                            for element in row:
                                if 'Mfg Data (ASCII)' in element:
                                    serial_num = element[serial_index:]
                                    mod_num = re.sub(r'\W+', '', serial_num).upper()
                                    if mod_num != '':
                                        serials_in_csv.append(mod_num)  # Serials in CSV will all be regex version
                                        mod_set.add((mod_num, serial_num))  # Adding tuple with the regex and non-regex version
                                    else:
                                        pass
                                else:
                                    pass
                    modules_by_date[ordered_dates[i]] = serials_in_csv  # Date to list of serials
                # Purpose of this section is just to get a module number associated with start and end date
                for serial_tuple in mod_set:  # Look through every serial number in bus
                    count = 0
                    first_date = ''
                    latest_date = ''
                    start_end_list = []
                    base_serial = serial_tuple[0]  # Current serial of interest
                    
                    for each_date in ordered_dates:  # For each date (keys to current_date_serials dictionary)
                        current_date_serials = modules_by_date[each_date]  # Getting list of the serials for current CSV/date
                        for comp_serial in current_date_serials:
                            if base_serial == comp_serial:  # Compare base serial to comparison serial 
                                count += 1
                                latest_date = each_date
#                                 print("Current date: ", each_date, "\nCurrent latest date: ", latest_date)
                                if count == 1:
                                    first_date = each_date
                                    start_end_list.append(first_date)
                                else:
                                    pass
                    start_end_list.append(latest_date)
                    serial_start_end[serial_tuple[1]] = start_end_list  # Uncleaned serial -> start and end dates
                    
#                 # Now compare start and end dates for each module to the first and last date of the ordered_csvs by date list

#                 pprint.pprint(serial_start_end)  # For pretty printing dictionary
#                 print("Length of the serial dictionary: ", len(serial_start_end), "\nLength of mod set: ", len(mod_set))
                for serial_key in serial_start_end:
                    start_end = serial_start_end[serial_key]
#                     print(start_end)
# #                     print('Key : ', serial_key, "\nStart and End Dates: ", start_end, "\n")
#                     print("Start Date: ", start_end[0], "\nFirst Date: ", ordered_dates[0], "\nEnd Date: ", start_end[-1],  "\nLast Date: ", ordered_dates[-1], "\n")
                    if start_end[0] != ordered_dates[0] and start_end[-1] != ordered_dates[-1]:
                        replaced_mods.add(serial_key)
                bus_swapped_mods[bus] = replaced_mods
#                 print(replaced_mods)
    return {k:v for k,v in bus_swapped_mods.items() if v}


In [107]:
replaced_mods = find_replaced_modules(directory)
replaced_mods

{'bus_1': {' 364A1585G3REV--13G2284..........'},
 'bus_111': {' 0039-1613-0QD-402335-00710......'},
 'bus_122': {" 0039-1535-0CW-402335-00710..'..."},
 'bus_15': {' 13K2474.........................'},
 'bus_2': {' 0039-1811-00U-402335-00804......'},
 'bus_25': {' 0039-1510-06B-402335-00710......',
  ' 0039-1512-0E9-402335-00710......',
  ' 364A1585G3REVC-14K1885..........'},
 'bus_28': {" 0039-1634-04H-402335-00802..'..."},
 'bus_32': {' 364A1585G2REVA-13K2342..........'},
 'bus_36': {' 364A1585G3REVB-14E6785..........',
  ' 364A1585G3REVB-14E6891..........',
  ' 364A1585G3REVB-14F7320..........'},
 'bus_40': {' 0039-1638-0HC-402335-00802..&...'},
 'bus_58': {' 0039-1630-0GB-402335-00710......'},
 'bus_6': {' 0039-1609-009-402335-00710......'},
 'bus_77': {' 0039-1434-03J-402335-00710......',
  " 0039-1635-06T-402335-00802..'..."},
 'bus_78': {' 0039-1632-04H-402335-00710......'},
 'bus_85': {' 0039-1639-061-402335-00802..&...'},
 'bus_87': {' 364A1585G3REVC-14K2029..........'}}

In [109]:
count = 0
for bus in replaced_mods:
    serial_nums = replaced_mods[bus]
    count += len(serial_nums)
count

21

In [ ]:
# Bus 62

In [ ]:
# Changes needed: convert all of the module numbers to lowercase and only alphanumerics. 
# Grab all modules and place into one set.
# If the file is the first file, then add to the first list
# If the file is the last list, then add to the last list.
# For each serial in the all modules set, check that the module number is not in the first and last serial lists
# If that is the case, then append that module to replaced mods list
'''
Would have to find all serial numbers for each file and then check that they don't appear in all the files behind them(but do in
some of the files), and then also need to check that they disppear later on.
Conversely, you can check that they have a date that they first appear and then a date that they end
Maybe make a table of the serial numbers with the start date of the files and the end date of the files
and then the serial numbers will have their own when they first appeared and when they last appeared


Can create a tuple with the serial number and the start and end date.
Need a set of all the modules, then for each module in there, iterate over a list of all the modules for each CSV,
when it first appears, 

Create a set of all the module numbers.
Create a dictionary with the date as the key for the file, then a list of serial numbers for that date.
Create a counter that starts at 0. If the module number is in the list correspondong to a date, then count += 1.
Create a separate dictionary for each serial number
If the count is 1, then set that date (dictionary key corresponding to the list) as the start date, and then append to that 
specific module number's list
Each time the module number appears, set the date that it appears most recently as the latest date. 
After the for loop over all the dates and their corresponding module lists, take that latest date and append it to that specific
module number's list
For each module, if the start date is not the first date in the ordered dates and the latest date is not the last date
in the ordered dates list, then that means it appeared somewhere in the middle, therefore it was swapped in and out.

List of things we know:




- The serial number cannot appear in the first file
- A new serial can appear in the final CSV if the module is swapped out in the CSV before the last file
- but then this also means that the modules in the last file don't matter at all.
- START DATE must be between the first file and the second to last file
- Ignore the serials in the first file, but cannot ignore the serials that appear in the last file
'''

In [6]:
replaced_modules = find_replaced_modules(directory)

In [7]:
for folder in listdir(directory):
    if folder.startswith('bus'):
        print(replaced_modules[folder])

[' 364A1585G3REV--13G2284..........']
[]
[]
[]
[' 0039-1639-061-402335-00802..&...']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[' 0039-1613-0QD-402335-00710......']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[" 0039-1535-0CW-402335-00710..'..."]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[' 0039-1811-00U-402335-00804......']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[' 0039-1510-06B-402335-00710......', ' 364A1585G3REVC-14K1885..........', ' 0039-1512-0E9-402335-00710......']
[]
[]
[" 0039-1634-04H-402335-00802..'..."]
[]
[]
[]
[]
[' 364A1585G2REVA-13K2342..........']
[]
[]
[]
[' 364A1585G3REVB-14F7320..........', ' 364A1585G3REVB-14E6891..........', ' 364A1585G3REVB-14E6785..........']
[]
[]
[' 0039-1638-0HC-402335-00802..&...']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[' 0039-1630-0GB-402335-00710......']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[' 0039-1609-009-402335-00710......']
[]
[]
[]
[]
[" 0039-1635-06T-402335-00802..'...", ' 0039-1434-03J-402335-00710......

In [8]:
# Want to look for modules that do not appear in the first file and that do not appear in the last file
# Also want to look for folders where there are more than two files
# Want to save the module number, the datafiles of entrance and exit,

In [9]:
# Read each line of the CSV into a dataframe and then try to match the ASCII numbers
# grab the iloc number or do df.iterrow -> find the index, then grab the next x amount of indices.
# Need to create tables for all of the features...
#     Cell voltages, cell balancers, 

In [10]:
directory_test = directory + 'bus_1/' + '0035_ProfileData_20160926060714.csv'
df_rows = []
with open(directory_test) as file:
    reader = csv.reader(file)
    for row in reader:
        filtered_row = [element for element in row if element]
        df_rows.append(filtered_row)
df_test = pd.DataFrame(df_rows)
df_test

0     1     2     3     4     5   \
0                                       None  None  None  None  None  None   
1    ESS BMS and Battery Module Profile Data  None  None  None  None  None   
2                                       None  None  None  None  None  None   
3      Data retrieved: 09/26/2016 @ 06:07:22  None  None  None  None  None   
4                                       None  None  None  None  None  None   
..                                       ...   ...   ...   ...   ...   ...   
955                                     None  None  None  None  None  None   
956                    <Module Voltages (V)>  None  None  None  None  None   
957                                     None  None  None  None  None  None   
958                                   < 24.0  24.0  26.4  28.8  31.2  33.6   
959                                              0     0     0    13  7600   

         6        7         8        9   ...    64    65    66    67    68  \
0      None     None      None     None  ...  None  None  None  None  None   
1      None     None      None     None  ...  None  None  None  None  None   
2      None     None      None     None  ...  None  None  None  None  None   
3      None     None      None     None  ...  None  None  None  None  None   
4      None     None      None     None  ...  None  None  None  None  None   
..      ...      ...       ...      ...  ...   ...   ...   ...   ...   ...   
955    None     None      None     None  ...  None  None  None  None  None   
956    None     None      None     None  ...  None  None  None  None  None   
957    None     None      None     None  ...  None  None  None  None  None   
958    36.0     38.4      40.8     43.2  ...  None  None  None  None  None   
959  903587  4093273  22635681  3267632  ...  None  None  None  None  None   

       69    70    71    72    73  
0    None  None  None  None  None  
1    None  None  None  None  None  
2    None  None  None  None  None  
3    None  None  None  None  None  
4    None  None  None  None  None  
..    ...   ...   ...   ...   ...  
955  None  None  None  None  None  
956  None  None  None  None  None  
957  None  None  None  None  None  
958  None  None  None  None  None  
959  None  None  None  None  None  

[960 rows x 74 columns]

In [11]:
pd.set_option("display.max_rows", None, "display.max_columns", None)
HTML(df_test.to_html(index=False))

In [27]:
keyword = 'Mfg Data'
serial_num = 'Mfg Data (ASCII): 0039-1449-0BD-402335-00710..1...'
mod_num = re.sub(r'\W+', '', serial_num[17:]).upper()
characteristic = 'Current'
# for index, row in df_test.iterrows():
#     print(row)
row_list = []
for index, row in df_test.iterrows():
    row_to_list = row.tolist()
    row_list.append(row_to_list)
for i in range(len(row_list)):
    for element in row_list[i]:
        if element is not None:
            if keyword in element:
                mod_num_test = re.sub(r'\W+', '', element[17:]).upper()
                if mod_num_test == mod_num:
                    title= row_list[i+5][0] # Concatenate with Module Number (key to dictionary)
                    column_labels = row_list[i + 7][1:]
                    data_vals = []
                    row_labels = []
                    for j in range(8, 20):
                        data_vals.append(row_list[i + j][1:])
                        row_labels.append(row_list[i + j][0])
                    df_current = pd.DataFrame(data=data_vals, columns=column_labels, index=row_labels)
                    df_current.dropna(how='all', axis=1, inplace=True)
                    df_current = df_current.drop('TOTAL', 1)
                    df_current = df_current.rename(columns=str).rename(columns={'None':'TOTAL'})
df_current = df_current.style.set_caption("Hello World")
df_current

In [20]:
for file in listdir(directory + 'bus_1'):
    print(file)

.DS_Store
0035_ProfileData_20160926060714.csv
0035_ProfileData_20161114095559.csv
0035_ProfileData_20170203062513.csv
0035_ProfileData_20170411092927.csv
13L0035_ProfileData_20170919113854.csv
13L0035_ProfileData_20180118080858.csv


In [21]:
directory_test_2 = directory + 'bus_1/' + '13L0035_ProfileData_20170919113854.csv'
df_rows_2 = []
with open(directory_test_2) as file:
    reader = csv.reader(file)
    for row in reader:

        filtered_row = [element for element in row if element]
        df_rows_2.append(filtered_row)
df_test_2 = pd.DataFrame(df_rows_2)
df_test_2

0           1        2   \
0                                                             None     None   
1              ESS BMS and Battery Module Profile Data        None     None   
2                                                 None        None     None   
3                Data retrieved: 09/19/2017 @ 11:39:26        None     None   
4                                                 None        None     None   
5                             BMS Software AS version:  0x0206BA42     None   
6                            BMS Software AS checksum:  0x03EC9675     None   
7                             BMS Software OS version:  0x0206BB42     None   
8                            BMS Software OS checksum:  0xDF1C5EF9     None   
9                                                 None        None     None   
10                                                None        None     None   
11                                           Mfg Data:        0x33     0x36   
12                                                None        None     None   
13   Mfg Data (ASCII): 364A1583G100-13L0035...........        None     None   
14                                                None        None     None   
15                                                None        None     None   
16                               <Battery Current (A)>        None     None   
17                                                None        None     None   
18                                            < -350.0        -350     -340   
19                                                               0        0   
20                               <Battery Voltage (V)>        None     None   
21                                                None        None     None   
22                                             < 450.0         450      460   
23                                                             396        2   
24                                        <Power (kW)>        None     None   
25                                                None        None     None   
26                                            < -200.0        -200     -190   
27                                                               0        0   
28                            <A2D Error profile data>        None     None   
29                                                None        None     None   
30                                             CURRENT     VOLTAGE    POWER   
31                                                   0           0        0   
32                                                None        None     None   
33                                                None        None     None   
34                                            MODULE 1        None     None   
35                                                None        None     None   
36                                Software AS version:  0x0104CA42     None   
37                               Software AS checksum:  0x7A2CD716     None   
38                                Software OS version:  0x0104CB42     None   
39                               Software OS checksum:  0xC6B5EEBD     None   
40                                                None        None     None   
41                                           Mfg Data:        0x30     0x30   
42                                                None        None     None   
43   Mfg Data (ASCII): 0039-1449-0BD-402335-00710.....        None     None   
44                                                None        None     None   
45                                                None        None     None   
46                         A/D Conversion Error Count:           0     None   
47                                                None        None     None   
48                                 <Cell Voltages (V)>        None     None   
49                                                None        None     None   
50                     

# Function for creating dataframes for desired characteristic

### Function takes in characteristic argument. 

#### Please use one of the following

1. 'cell voltages' for acquiring data for the module cell (submodule) voltages.
2. 'balancers' for acquiring data for the module cell balancers.
3. 'temperatures' for acquiring data for the module temperatures.
4. 'module voltages' for acquiring data for the overall module voltages.

In [57]:
def swapped_mod_dataframes(directory, serial_num, characteristic):
    serial_index = 17
    mod_num = re.sub(r'\W+', '', serial_num[serial_index:]).upper()  # Convert the serial number provided
    keyword = 'Mfg Data'
    index_dictionary = {
        'cell voltages': [5, 7, 8, 20],
        'balancers': [21, 23, 24, 36],
        'temperatures': [37, 39, 40, 42],
        'module voltages': [43, 45, 46, 47]
#         Numbers correspond to the number of rows from the module number row that needs to be skipped in order to reach
#         the following: title_row, column_row, start_index of data values, end_index of values
    }
    key_list = index_dictionary.keys()
    list_bus_nums = []
    list_desired_dfs = []
    for file in listdir(directory):  # Place this file in directory with False_files -> Keiton's code
            if file.startswith('bus'):
                list_bus_nums.append(file)  # Getting list of bus names
    for bus in list_bus_nums:  # For each bus
        ordered_dates = []
        df = sort_bus_by_date.sort_bus_by_date(directory, bus + '/')
        ordered_csv = df['Filename'].tolist()
        ordered_unclean_dates = df['DateRetrieved'].tolist()
        for unclean_date in ordered_unclean_dates:
            split_results = unclean_date.strftime('%m/%d/%Y, %H:%M:%S')
            ordered_dates.append(split_results)
        for csv_file in range(len(ordered_csv)):  # Iterate over each csv file in the current bus folder
            directory_path = directory + bus + '/' + ordered_csv[csv_file]  # Convert this to file name (for file in bus folder)
#             df_rows = []
            row_list = []
            with open(directory_path) as file:  # Read in the CSV file specified as a list of rows
                reader = csv.reader(file)
                for row in reader:
                    row_list.append(row)
            for i in range(len(row_list)):  # For each row in row_list
                for element in row_list[i]:
                    if element is not None:
                        if keyword in element:
                            mod_num_test = re.sub(r'\W+', '', element[serial_index:]).upper()
                            if mod_num_test == mod_num:
#                                 print('Bus Number: ', bus, '\nDates: ', ordered_dates)
                                indices_list = index_dictionary[characteristic.lower()]
                                title = row_list[i + indices_list[0]][0] + '  ' + ordered_dates[csv_file]
                                # Concatenate with Module Number (key to dictionary)
                                column_labels = row_list[i + indices_list[1]][1:]
                                data_vals = []
                                row_labels = []
                                for j in range(indices_list[2], indices_list[3]):
                                    data_vals.append(row_list[i + j][1:])
                                    row_labels.append(row_list[i + j][0])
                                df_voltage = pd.DataFrame(data=data_vals, columns=column_labels, index=row_labels)
#                                     df_voltage.dropna(how='all', axis=1, inplace=True)
#                                     df_voltage = df_voltage.drop('TOTAL', 1)
#                                     df_voltage = df_voltage.rename(columns=str).rename(columns={'None':'TOTAL'})
#                                     df_voltage = df_voltage.style.set_caption(title)
                                index = df_voltage.index
                                index.name = title
                                list_desired_dfs.append(df_voltage)
    return list_desired_dfs

In [58]:
list_desired_dfs = swapped_mod_dataframes(directory, 'Mfg Data (ASCII): 0039-1449-0BD-402335-00710..1...', 'module voltages')
# list_desired_dfs[0].index.name
list_desired_dfs

[                                            < 24.0 24.0 26.4 28.8 31.2   33.6  \
 <Module Voltages (V)>  09/26/2016, 06:07:22                                     
                                                  0    0    0    0    9  87757   
 
                                                 36.0     38.4     40.8   43.2  \
 <Module Voltages (V)>  09/26/2016, 06:07:22                                     
                                              1882987  8937991  1370676  61534   
 
                                             45.6 >= 48.0       TOTAL  
 <Module Voltages (V)>  09/26/2016, 06:07:22                           
                                                0       0    12340954  ,
                                             < 24.0 24.0 26.4 28.8 31.2  \
 <Module Voltages (V)>  11/14/2016, 09:56:09                              
                                                  0    0    0    0    9   
 
                                                33.6     36.

In [16]:
# Layer the lines together with the swapped modules and the used modules
# For the check which modules are swapped out, you need to create a list of modules for the CSV that you are looking through and then


# Create lists for voltage, temperature, etc.
# Then use characteristic.lower() as the first substring word, add it to something like characteristic_index_rows
# So now you can use the characteristic passed in, concatenate with some phrase, and then that can be used to call on the 
# premade lists of indices for the rows that you want
# Prevents repetetive coding

[2, 3]

In [ ]:
# Convert this to for bus folder in directory
# Then use Sarah's code to grab the ordered list of CSV
# Then do for each bus folder and then for each name in that list and concatenate to directory

# Need a directory argument
# Need a module number argument
def swapped_mod_dataframes(directory, serial_num, characteristic):
    mod_num = re.sub(r'\W+', '', serial_num[serial_index:]).upper()  # Convert the serial number provided
    keyword = 'Mfg Data'
    serial_index = 17
    current_title_row_index = 5  # Rows needed to be skipped from ModNum to needed data for Current values.
    current_column_row_index = 7
    current_start_index = 8
    current_end_index = 20
    list_bus_nums = []
    for file in listdir(directory):  # Place this file in directory with False_files -> Keiton's code
            if file.startswith('bus'):
                list_bus_nums.append(file)  # Getting list of bus names
        for bus in list_bus_nums:  # For each bus
            ordered_dates = []
            df = sort_bus_by_date.sort_bus_by_date(directory, bus + '/')
            ordered_csv = df['Filename'].tolist()
            ordered_unclean_dates = df['DateRetrieved'].tolist()
            
            for csv_file in ordered_csv:  # Iterate over each csv file in the current bus folder
                directory_path = directory + bus + csv_file  # Convert this to file name (for file in bus folder)
                df_rows = []
                with open(directory_path) as file:  # Read in the CSV file specified as a list of rows
                    reader = csv.reader(file)
                    for row in reader:
                        filtered_row = [element for element in row if element]
                        df_rows.append(filtered_row)
                df_csv = pd.DataFrame(df_rows)
                row_list = []
                for index, row in df_test_2.iterrows():  # Create a list of the rows from the dataframe
                    row_to_list = row.tolist()
                    row_list.append(row_to_list)
                for i in range(len(row_list)):
                    for element in row_list[i]:
                        if element is not None:
                            if keyword in element:
                                mod_num_test = re.sub(r'\W+', '', element[serial_index:]).upper()
                                if mod_num_test == mod_num:
                                    title= row_list[i + current_title_row_index][0] # Concatenate with Module Number (key to dictionary)
                                    column_labels = row_list[i + current_column_row_index][1:]
                                    data_vals = []
                                    row_labels = []
                                    for j in range(current_start_index, current_end_index):
                                        data_vals.append(row_list[i + j][1:])
                                        row_labels.append(row_list[i + j][0])
                                    df_current_2 = pd.DataFrame(data=data_vals, columns=column_labels, index=row_labels)
                                    df_current_2.dropna(how='all', axis=1, inplace=True)
                                    df_current_2 = df_current_2.drop('TOTAL', 1)
                                    df_current_2 = df_current_2.rename(columns=str).rename(columns={'None':'TOTAL'})
                df_current_2

In [48]:
df = pd.DataFrame({"Letters": ["a", "b", "c"], "Numbers": [1, 2, 3]})
index = df.index
index.name = "Index Title"

print(df)
# index

            Letters  Numbers
Index Title                 
0                 a        1
1                 b        2
2                 c        3


In [69]:
a = set()
a.add((1, 2))
a.add((2, 3))
a.add((1, 2))
for rand_tup in a:
    print(rand_tup[0])

2
1


In [102]:
default = {'a': ['alpha'], 'b': ['beta','gamma'], 'g': []}
new_dict = {k:v for k,v in default.items() if v}
new_dict

{'a': ['alpha'], 'b': ['beta', 'gamma']}